In [25]:
import matplotlib.pyplot as plt
%matplotlib inline
import json
import requests
from datetime import timedelta, datetime
from operator import itemgetter
import pandas as pd
import numpy as np

def createOlapPayload(sources,metrics,dimensions,startDate,endDate,filters):
	data = {}
	data['sources'] = sources
	data['metrics'] = metrics
	i = 1
	dimensionsDict = {}
	for dimension in dimensions:
		dimensionsDict[dimension] = i
		i += 1
	data['dimensions'] = dimensionsDict
	date1 = datetime.strptime(startDate,'%Y-%m-%d').strftime("%Y-%m-%d")
	date2 = (datetime.strptime(endDate,'%Y-%m-%d') + timedelta(1)).strftime("%Y-%m-%d")
	segments = []
	segmentsDict = {}
	segmentsDict['dateStart'] = "{0}T00:00:00+03:00".format(date1)
	segmentsDict['dateEnd'] = "{0}T00:00:00+03:00".format(date2)
	segmentsDict['filters'] = {}
	for filterKey, filterValue in filters.iteritems():
		segmentsDict['filters'][filterKey] = {}
		segmentsDict['filters'][filterKey]['type'] = 'DIMENSION'
		segmentsDict['filters'][filterKey]['ids'] = filterValue
	segments.append(segmentsDict)
	data['segments'] = segments
	return data

def getJSONOlapResponse(data):
	url = 'http://192.168.10.6:4000/api/OLAP/Plain'
	headers = {'Content-Type': 'application/json'}
	response = requests.post(url,data,headers=headers)
	return response.text

def transformOlapResponse(response,payload):
	data = []
	dimensionsList = [{'key': k, 'value': v} for k,v in payload['dimensions'].iteritems()]
	dimensionsList = sorted(dimensionsList, key=itemgetter('value'))
	for item in response:
		i = 0
		dataDict = {}
		for dimensionValue in item['dimensions']:
			dimensionName = dimensionsList[i]['key']
			dataDict[dimensionName] = dimensionValue
			i += 1
		metrics = item['value'][0]
		for k,v in metrics.iteritems():
			dataDict[k] = v
		data.append(dataDict)
	return data

In [26]:
filters = {'campaignTypeId': ['1','2'], 'campaignExternalId': ['16251639','16350742','14959198','14959200','14959202','14248951','14258619','16455287','16455762','16456003',
                                                               '16456125','16456278','16470199','16470748','15534590','15537079','15537368','15539555','16435957','16436018']}
sources = ["direct_conversion","metrika"]
metrics = ["clicks","shows","spent","visits","cpaVisits","rejectPercent"]
dimensions = ['campaignExternalId','campaignName','keyPhraseName','keyPhraseExternalId']
startDate = '2016-02-04'
endDate = '2016-03-04'
payload = createOlapPayload(sources,metrics,dimensions,startDate,endDate,filters)
response = getJSONOlapResponse(json.dumps(payload))
# data = transformOlapResponse(response,payload)

In [27]:
response

u'[{"dimensions":["14248951","okna-okoshkino \u041f\u043e\u0438\u0441\u043a 2 \u0412\u043e\u043b\u0433\u043e\u0433\u0440\u0430\u0434","!rehau !\u0432 !\u043c\u043e\u0441\u043a\u0432\u0435","5046069873"],"value":[{"visits":0.0,"goalVisits":0.0,"shows":0.0,"spent":0.0,"clicks":0.0,"cpaVisits":0.0,"rejectPercent":0.0}]},{"dimensions":["14248951","okna-okoshkino \u041f\u043e\u0438\u0441\u043a 2 \u0412\u043e\u043b\u0433\u043e\u0433\u0440\u0430\u0434","!rehau","5046069874"],"value":[{"visits":0.0,"goalVisits":0.0,"shows":60.0,"spent":19.350000381469727,"clicks":1.0,"cpaVisits":0.0,"rejectPercent":0.0}]},{"dimensions":["14248951","okna-okoshkino \u041f\u043e\u0438\u0441\u043a 2 \u0412\u043e\u043b\u0433\u043e\u0433\u0440\u0430\u0434","!\u0410\u0434\u0440\u0435\u0441\u0430 !\u043c\u0430\u0433\u0430\u0437\u0438\u043d\u043e\u0432 !\u043f\u043b\u0430\u0441\u0442\u0438\u043a\u043e\u0432\u044b\u0445 !\u043e\u043a\u043e\u043d","5046068462"],"value":[{"visits":0.0,"goalVisits":0.0,"shows":0.0,"spent":

In [18]:
df = pd.DataFrame(data)

In [19]:
df

campaignExternalId                      campaignName  clicks  cpaVisits  \
0               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
1               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
2               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
3               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
4               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
5               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
6               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
7               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
8               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
9               14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
10              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
11              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
12              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
13              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
14              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
15              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
16              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
17              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
18              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
19              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
20              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
21              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
22              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
23              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
24              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
25              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
26              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
27              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
28              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
29              14248951  okna-okoshkino Поиск 2 Волгоград       0          0   
...                  ...                               ...     ...        ...   
17741           16470748       okna-okoshkino Поиск Ростов       0          0   
17742           16470748       okna-okoshkino Поиск Ростов       0          0   
17743           16470748       okna-okoshkino Поиск Ростов       0          0   
17744           16470748       okna-okoshkino Поиск Ростов       0          0   
17745           16470748       okna-okoshkino Поиск Ростов       0          0   
17746           16470748       okna-okoshkino Поиск Ростов       0          0   
17747           16470748       okna-okoshkino Поиск Ростов       0          0   
17748           16470748       okna-okoshkino Поиск Ростов       0          0   
17749           16470748       okna-okoshkino Поиск Ростов       0          0   
17750           16470748       okna-okoshkino Поиск Ростов       0          0   
17751           16470748       okna-okoshkino Поиск Ростов       0          0   
17752           16470748       okna-okoshkino Поиск Ростов       0          0   
17753           16470748       okna-okoshkino Поиск Ростов       0          0   
17754           16470748       okna-okoshkino Поиск Ростов       0          0   
17755           16470748       okna-okoshkino Поиск Ростов       0          0   
17756           16470748       okna-okoshkino Поиск Ростов       0          0   
17757           16470748       okna-okoshkino Поиск Ростов       0          0   
17758           16470748       okna-o

In [10]:
len(df)

7814

In [11]:
filters = {}
sources = ["direct_conversion"]
metrics = ["clicks","shows","spent"]
dimensions = ['project','campaignExternalId','campaignName','keyPhraseName','keyPhraseExternalId']
startDate = '2016-03-25'
endDate = '2016-04-07'
payload = createOlapPayload(sources,metrics,dimensions,startDate,endDate,filters)
response = getJSONOlapResponse(json.dumps(payload))
data = transformOlapResponse(response,payload)
df2 = pd.DataFrame(data)

ConnectionError: ('Connection aborted.', BadStatusLine("''",))